# streaming dataset sampler

for https://hf.co/datasets/LLM360/TxT360


In [ ]:
!nproc
!free -h

96
               total        used        free      shared  buff/cache   available
Mem:           334Gi       1.9Gi       315Gi       2.0Mi        16Gi       330Gi
Swap:             0B          0B          0B


In [ ]:
!pip install -q ninja
!pip install -U -q transformers datasets accelerate sentencepiece
from huggingface_hub import notebook_login
# notebook_login()

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 307.2/307.2 kB 4.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.4/44.4 kB 1.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 52.8/52.8 kB 2.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.9/9.9 MB 77.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 471.6/471.6 kB 22.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 330.9/330.9 kB 19.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 8.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 177.6/177.6 kB 14.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 53.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.9/2.9 MB 72.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 9.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 13.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2

In [ ]:
!pip install fasttext-langdetect tiktoken -q

  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 73.4/73.4 kB 2.0 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 18.1 MB/s eta 0:00:00


In [ ]:
import tiktoken
enc = tiktoken.get_encoding("cl100k_base")
assert enc.decode(enc.encode("hello world")) == "hello world"

# To get the tokeniser corresponding to a specific model in the OpenAI API:
enc = tiktoken.encoding_for_model("gpt-4")

In [ ]:
from pathlib import Path
import random
import os
from datasets import Dataset, load_dataset
from tqdm.auto import tqdm
from transformers import AutoTokenizer
from datasets import DownloadConfig
from ftlangdetect import detect
import re

MIN_LENGTH_TOKENS = 256
MAX_LENGTH_TOKENS = 8192

cfg = DownloadConfig(max_retries=20, extract_on_the_fly=True)

print(f"min_length_tokens: {MIN_LENGTH_TOKENS}")
print(f"max_length_tokens: {MAX_LENGTH_TOKENS}")

# @title define core fns

def get_workers():
    return max(1, int(os.cpu_count() //2))

def normalize_text(text):
    """
    # Example usage
    original_text = "This is a\nsample   text with\n\nmultiple   spaces."
    normalized_text = normalize_text(original_text)
    print(normalized_text)

    Args:
        text (TYPE): Description

    Returns:
        TYPE: Description
    """
    text = str(text)
    # Remove newlines
    text = text.replace("\n", " ")

    # Normalize whitespace
    text = re.sub(r"\s+", " ", text)

    return text


def get_lang(text):
    """langdetect wrapper

    Args:
        example (TYPE): Description

    Returns:
        TYPE: Description
    """
    text = str(text)

    if len(text) < 3:
        return "unknown"

    try:
        return detect(text=normalize_text(text)[:5000])["lang"]
    except Exception as e:
        return "unknown-error"


def is_en(text: str):

    return get_lang(text) == "en"


def is_length_appropriate(
    text,
    tokenizer,
    min_length: int = MIN_LENGTH_TOKENS,
    max_length: int = MAX_LENGTH_TOKENS,
):
    """
    Check if the tokenized text length falls within specified bounds.

    Args:
        text (str): The text to be tokenized.
        tokenizer: Tokenizer object.
        min_length (int): Minimum token length.
        max_length (int): Maximum token length.

    No Longer Returned:
        bool: True if text length is appropriate, False otherwise.
    """
    tokenized = enc.encode(text)
    token_length = len(tokenized)
    return min_length < token_length < max_length


def save_dataset(dataset, save_path):
    """
    Save the dataset to the specified path.

    Args:
        dataset: The dataset to save.
        save_path (str): Path to save the dataset.
    """
    save_path = Path(save_path)
    dataset.save_to_disk(str(save_path), num_proc=get_workers())
    print(f"Dataset saved to {save_path}")


def main(
    dataset_name,
    config_name="default",
    text_column="text",
    save_path: str = None,
    tokenizer_name="meta-llama/Meta-Llama-3-8B",
    check_lang: bool = True,
    max_samples=500,
    min_length_chars: int = None,
):
    """
    Main function to process and save the dataset.

    Args:
        dataset_name (str): Name of the dataset.
        config_name (str, optional): Description
        text_column (str, optional): Description
        save_path (str, optional): Path to save the processed dataset.
        tokenizer_name (str): Name of the tokenizer.
        max_samples (int): Maximum number of samples to save.
    """
    ds_short_name = dataset_name.split("/")[-1]
    min_length_chars = min_length_chars or MIN_LENGTH_TOKENS

    # Load the tokenizer
    tokenizer = AutoTokenizer.from_pretrained(tokenizer_name)

    # Load the dataset in streaming mode
    streaming_dataset = load_dataset(
        dataset_name, config_name, split="train", streaming=True,
        download_config=cfg
    ).shuffle(seed=random.SystemRandom().randint(69, 2**32) - 1)

    # Initialize variables for filtered data
    filtered_texts = []

    # Process the dataset
    for sample in tqdm(streaming_dataset, desc="Processing Dataset"):
        try:
            if min_length_chars:
                # fast check first
                if len(sample[text_column]) < min_length_chars:
                    continue

            # check length
            if is_length_appropriate(sample[text_column], tokenizer):

                filtered_texts.append(sample)
        except Exception as e:
            _txt = str(sample[text_column])[:200]
            print(f"Error checking sample: {_txt}  ...:\t{e}")
        # Stop after collecting max_samples
        if len(filtered_texts) == max_samples:
            print(f"hit max samples: {max_samples}")
            break

    # Create a dataset from the filtered texts
    # filtered_dataset = Dataset.from_dict({"text": filtered_texts})
    filtered_dataset = Dataset.from_list(filtered_texts)

    # Save the dataset
    max_samples = len(filtered_texts)
    save_path = (
        save_path
        or Path("exported-datasets") / f"{ds_short_name}_filtered-{max_samples}-samples"
    )
    save_path = Path(save_path)
    save_path.mkdir(parents=True, exist_ok=True)
    print(f"Saving dataset to {save_path}...")
    save_dataset(filtered_dataset, save_path)

    print("done!")

    return save_path

/usr/local/lib/python3.10/dist-packages/torch_xla/__init__.py:202: UserWarning: `tensorflow` can conflict with `torch-xla`. Prefer `tensorflow-cpu` when using PyTorch/XLA. To silence this warning, `pip uninstall -y tensorflow && pip install tensorflow-cpu`. If you are in a notebook environment such as Colab or Kaggle, restart your notebook runtime afterwards.
  warnings.warn(


min_length_tokens: 256
max_length_tokens: 8192


# run sampling

In [ ]:
ds_name = "LLM360/TxT360" # @param {type:"string"}
max_samples = 1000000 # @param {type:"integer"}
check_lang = False # @param {type:"boolean"}
short_ds_name = ds_name.split('/')[-1]
print(ds_name)
print(f"max_samples:\t{max_samples}")

output_path = main(
    ds_name,
    config_name='default',
    text_column='text',
    max_samples=max_samples,
    check_lang=check_lang
    )


LLM360/TxT360
max_samples:	1000000


tokenizer_config.json:   0%|          | 0.00/50.6k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.09M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/73.0 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/6.74k [00:00<?, ?B/s]

Resolving data files:   0%|          | 0/94301 [00:00<?, ?it/s]

Processing Dataset: 0it [00:00, ?it/s]

hit max samples: 1000000
Saving dataset to exported-datasets/TxT360_filtered-1000000-samples...


Saving the dataset (0/11 shards):   0%|          | 0/1000000 [00:00<?, ? examples/s]

Dataset saved to exported-datasets/TxT360_filtered-1000000-samples
done!


## load and push

In [ ]:
from datasets import load_from_disk

ds = load_from_disk(str(output_path.resolve()))
ds

Dataset({
    features: ['text', 'meta', 'subset'],
    num_rows: 1000000
})

In [ ]:
from google.colab import runtime

max_samples = round(max_samples / 1000)
MIN_LENGTH_TOKENS = round(MIN_LENGTH_TOKENS / 1000)
ds.shuffle().push_to_hub(
    f"BEE-spoke-data/{short_ds_name}-{max_samples}k-sample-{MIN_LENGTH_TOKENS}k_{MAX_LENGTH_TOKENS}k",
    private=True,
)

runtime.unassign()

Uploading the dataset shards:   0%|          | 0/11 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/91 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/91 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/91 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/91 [00:00<?, ?ba/s]

...

Creating parquet from Arrow format:   0%|          | 0/91 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/91 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/91 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/91 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/91 [00:00<?, ?ba/s]